In [1]:
import xlrd  # Read Excel files
import json  # Handle JSON data
import os  # Perform file operations
import numpy as np  # Numerical computations
import pandas as pd  # Handle tabular data
from qsar_ad.applicability_domain import kNNDomain  # Applicability domain calculation
from rdkit.Chem import AllChem  # Chemistry computation library
from rdkit import Chem  # Handle molecular structures
from rdkit.Chem import rdChemReactions  # Handle chemical reactions
from rdkit.DataStructs.cDataStructs import ConvertToNumpyArray  # Convert data structures
from rdkit import Chem as rdChem  # Re-import for convenience
from rdkit.Chem import Descriptors  # Compute chemical descriptors
from rdkit.Chem import rdMolDescriptors  # Compute molecular descriptors
from rdkit.Chem import Fragments  # Handle molecular fragments
from rdkit.Chem.rdMolDescriptors import GetMorganFingerprintAsBitVect  # Compute Morgan fingerprints
from rdkit.Chem.rdMolDescriptors import GetMACCSKeysFingerprint  # Compute MACCS fingerprints
from rdkit.ML.Descriptors import MoleculeDescriptors  # Compute ML descriptors
from rdkit.Chem.EState import Fingerprinter  # Compute E-State fingerprints
from rdkit.Chem import PandasTools  # Handle chemistry data in Pandas
from rdkit.Chem import MACCSkeys  # Compute MACCS fingerprints
from rdkit.Chem.rdMHFPFingerprint import MHFPEncoder  # Compute MHFP fingerprints
from rdkit.Chem import DataStructs  # Handle data structures
from rdkit.Chem.MolStandardize import rdMolStandardize  # Standardize molecular structures

In [2]:
def standardize_smi(smiles, basicClean=True, clearCharge=True, clearFrag=True, canonTautomer=True, isomeric=False):
    """
    Standardize a SMILES string.
    
    Parameters:
    smiles: str - The SMILES string to be standardized.
    basicClean: bool - Perform basic cleanup (remove H, metals, etc.).
    clearCharge: bool - Remove charges.
    clearFrag: bool - Remove molecular fragments.
    canonTautomer: bool - Canonicalize tautomers.
    isomeric: bool - Retain isomeric information.
    """
    try:
        clean_mol = Chem.MolFromSmiles(smiles)  # Convert SMILES string to RDKit molecule
        
        if basicClean:
            clean_mol = rdMolStandardize.Cleanup(clean_mol)  # Remove H, metals, and standardize
        
        if clearFrag:
            clean_mol = rdMolStandardize.FragmentParent(clean_mol)  # Keep only the main molecule
        
        if clearCharge:
            uncharger = rdMolStandardize.Uncharger()  # Create an uncharger object
            clean_mol = uncharger.uncharge(clean_mol)  # Remove charges
        
        stan_smiles = Chem.MolToSmiles(clean_mol, isomericSmiles=isomeric)  # Convert to standardized SMILES
        
    except Exception as e:
        print(e, smiles)  # Print error message and SMILES string
        return None
    
    return stan_smiles  # Return the standardized SMILES

In [3]:
# Read SMILES data from 'gaba_smi.csv'
smiles_lst = [i.split(',')[0] for i in open('../data/gaba_smi.csv').readlines()[1:]]

In [5]:
# Standardize the SMILES list
ecoinvent_mol_lst = [standardize_smi(c) for c in smiles_lst]

[00:50:25] Initializing MetalDisconnector
[00:50:25] Running MetalDisconnector
[00:50:25] Initializing Normalizer
[00:50:25] Running Normalizer
[00:50:25] Initializing MetalDisconnector
[00:50:25] Running MetalDisconnector
[00:50:25] Initializing Normalizer
[00:50:25] Running Normalizer
[00:50:25] Running LargestFragmentChooser
[00:50:25] Fragment: NCCCC(=O)O
[00:50:25] New largest fragment: NCCCC(=O)O (16)
[00:50:25] Running Uncharger
[00:50:25] Initializing MetalDisconnector
[00:50:25] Running MetalDisconnector
[00:50:25] Initializing Normalizer
[00:50:25] Running Normalizer
[00:50:25] Initializing MetalDisconnector
[00:50:25] Running MetalDisconnector
[00:50:25] Initializing Normalizer
[00:50:25] Running Normalizer
[00:50:25] Running LargestFragmentChooser
[00:50:25] Fragment: CC1CCC(C(C)C)C(O)C1
[00:50:25] New largest fragment: CC1CCC(C(C)C)C(O)C1 (31)
[00:50:25] Running Uncharger
[00:50:25] Initializing MetalDisconnector
[00:50:25] Running MetalDisconnector
[00:50:25] Initializing

[00:50:25] Initializing Normalizer
[00:50:25] Running Normalizer
[00:50:25] Running LargestFragmentChooser
[00:50:25] Fragment: O=C(O)CCC(=O)OC1N=C(c2ccccc2Cl)c2cc(Br)ccc2NC1=O
[00:50:25] New largest fragment: O=C(O)CCC(=O)OC1N=C(c2ccccc2Cl)c2cc(Br)ccc2NC1=O (42)
[00:50:25] Running Uncharger
[00:50:25] Initializing MetalDisconnector
[00:50:25] Running MetalDisconnector
[00:50:25] Initializing Normalizer
[00:50:25] Running Normalizer
[00:50:25] Initializing MetalDisconnector
[00:50:25] Running MetalDisconnector
[00:50:25] Initializing Normalizer
[00:50:25] Running Normalizer
[00:50:25] Running LargestFragmentChooser
[00:50:25] Fragment: O=C1CN=C(c2ccccc2)c2c(sc3c2CCCC3)N1
[00:50:25] New largest fragment: O=C1CN=C(c2ccccc2)c2c(sc3c2CCCC3)N1 (37)
[00:50:25] Running Uncharger
[00:50:25] Initializing MetalDisconnector
[00:50:25] Running MetalDisconnector
[00:50:25] Initializing Normalizer
[00:50:25] Running Normalizer
[00:50:25] Initializing MetalDisconnector
[00:50:25] Running MetalDisconn

[00:50:25] Initializing MetalDisconnector
[00:50:25] Running MetalDisconnector
[00:50:25] Initializing Normalizer
[00:50:25] Running Normalizer
[00:50:25] Running LargestFragmentChooser
[00:50:25] Fragment: On1cc(C2CCNCC2)c(-c2ccccc2)n1
[00:50:25] New largest fragment: On1cc(C2CCNCC2)c(-c2ccccc2)n1 (35)
[00:50:25] Running Uncharger
[00:50:25] Initializing MetalDisconnector
[00:50:25] Running MetalDisconnector
[00:50:25] Initializing Normalizer
[00:50:25] Running Normalizer
[00:50:25] Initializing MetalDisconnector
[00:50:25] Running MetalDisconnector
[00:50:25] Initializing Normalizer
[00:50:25] Running Normalizer
[00:50:25] Running LargestFragmentChooser
[00:50:25] Fragment: CCOC(=O)c1ncn2c1C1CCCN1C(=O)c1cc(OC)ccc1-2
[00:50:25] New largest fragment: CCOC(=O)c1ncn2c1C1CCCN1C(=O)c1cc(OC)ccc1-2 (44)
[00:50:25] Running Uncharger
[00:50:25] Initializing MetalDisconnector
[00:50:25] Running MetalDisconnector
[00:50:25] Initializing Normalizer
[00:50:25] Running Normalizer
[00:50:25] Initial

[00:50:25] Initializing MetalDisconnector
[00:50:25] Running MetalDisconnector
[00:50:25] Initializing Normalizer
[00:50:25] Running Normalizer
[00:50:25] Running LargestFragmentChooser
[00:50:25] Fragment: COc1cc(CNC2C3C4CC5C6C4CC3C6C52)cc(OC)c1OC
[00:50:25] New largest fragment: COc1cc(CNC2C3C4CC5C6C4CC3C6C52)cc(OC)c1OC (52)
[00:50:25] Running Uncharger
[00:50:25] Initializing MetalDisconnector
[00:50:25] Running MetalDisconnector
[00:50:25] Initializing Normalizer
[00:50:25] Running Normalizer
[00:50:25] Initializing MetalDisconnector
[00:50:25] Running MetalDisconnector
[00:50:25] Initializing Normalizer
[00:50:25] Running Normalizer
[00:50:25] Running LargestFragmentChooser
[00:50:25] Fragment: CC(COc1ccn(-c2ccc(F)cc2)c(=O)c1)Oc1ccccc1
[00:50:25] New largest fragment: CC(COc1ccn(-c2ccc(F)cc2)c(=O)c1)Oc1ccccc1 (43)
[00:50:25] Running Uncharger
[00:50:25] Initializing MetalDisconnector
[00:50:25] Running MetalDisconnector
[00:50:25] Initializing Normalizer
[00:50:25] Running Normali

In [6]:
# Compute Morgan fingerprints (radius=1024) and convert to numpy array
Xtrain = np.array(
    [AllChem.GetMorganFingerprintAsBitVect(x, radius=1024) for x in list(map(Chem.MolFromSmiles, ecoinvent_mol_lst))]
)

In [7]:
# Compute Applicability Domain
ad_domain = kNNDomain(Xtrain)

In [8]:
ad_domain.ad_threshold

11.539605396865621

In [11]:
# Read SMILES data from 'plant_smi.csv'
plant_list = [i.split(',')[0] for i in open('../data/plant_smi.csv').readlines()[1:]]

In [13]:
# Standardize the SMILES data
good_lst_std = [standardize_smi(c) for c in plant_list]

[00:51:07] Initializing MetalDisconnector
[00:51:07] Running MetalDisconnector
[00:51:07] Initializing Normalizer
[00:51:07] Running Normalizer
[00:51:07] Initializing MetalDisconnector
[00:51:07] Running MetalDisconnector
[00:51:07] Initializing Normalizer
[00:51:07] Running Normalizer
[00:51:07] Running LargestFragmentChooser
[00:51:07] Fragment: CC(=O)CCCC(C)CCCC(C)CCCC(C)C
[00:51:07] New largest fragment: CC(=O)CCCC(C)CCCC(C)CCCC(C)C (55)
[00:51:07] Running Uncharger
[00:51:07] Initializing MetalDisconnector
[00:51:07] Running MetalDisconnector
[00:51:07] Initializing Normalizer
[00:51:07] Running Normalizer
[00:51:07] Initializing MetalDisconnector
[00:51:07] Running MetalDisconnector
[00:51:07] Initializing Normalizer
[00:51:07] Running Normalizer
[00:51:07] Running LargestFragmentChooser
[00:51:07] Fragment: CC(=O)CC(C)(C)O
[00:51:07] New largest fragment: CC(=O)CC(C)(C)O (20)
[00:51:07] Running Uncharger
[00:51:07] Initializing MetalDisconnector
[00:51:07] Running MetalDisconne

[00:51:08] Initializing MetalDisconnector
[00:51:08] Running MetalDisconnector
[00:51:08] Initializing Normalizer
[00:51:08] Running Normalizer
[00:51:08] Initializing MetalDisconnector
[00:51:08] Running MetalDisconnector
[00:51:08] Initializing Normalizer
[00:51:08] Running Normalizer
[00:51:08] Running LargestFragmentChooser
[00:51:08] Fragment: CC(C)=CCCC1(C)C2CC=C(C)C1C2
[00:51:08] New largest fragment: CC(C)=CCCC1(C)C2CC=C(C)C1C2 (39)
[00:51:08] Running Uncharger
[00:51:08] Initializing MetalDisconnector
[00:51:08] Running MetalDisconnector
[00:51:08] Initializing Normalizer
[00:51:08] Running Normalizer
[00:51:08] Initializing MetalDisconnector
[00:51:08] Running MetalDisconnector
[00:51:08] Initializing Normalizer
[00:51:08] Running Normalizer
[00:51:08] Running LargestFragmentChooser
[00:51:08] Fragment: CC1=CCC(C(C)C)=CC1
[00:51:08] New largest fragment: CC1=CCC(C(C)C)=CC1 (26)
[00:51:08] Running Uncharger
[00:51:08] Initializing MetalDisconnector
[00:51:08] Running MetalDisc

[00:51:08] Running MetalDisconnector
[00:51:08] Initializing Normalizer
[00:51:08] Running Normalizer
[00:51:08] Running LargestFragmentChooser
[00:51:08] Fragment: C=CC1(C)CCC(C(C)C)=CC1C(=C)C
[00:51:08] New largest fragment: C=CC1(C)CCC(C(C)C)=CC1C(=C)C (39)
[00:51:08] Running Uncharger
[00:51:08] Initializing MetalDisconnector
[00:51:08] Running MetalDisconnector
[00:51:08] Initializing Normalizer
[00:51:08] Running Normalizer
[00:51:08] Initializing MetalDisconnector
[00:51:08] Running MetalDisconnector
[00:51:08] Initializing Normalizer
[00:51:08] Running Normalizer
[00:51:08] Running LargestFragmentChooser
[00:51:08] Fragment: C=C(C)C1CCC2(C)CCC=C(C)C2C1
[00:51:08] New largest fragment: C=C(C)C1CCC2(C)CCC=C(C)C2C1 (39)
[00:51:08] Running Uncharger
[00:51:08] Initializing MetalDisconnector
[00:51:08] Running MetalDisconnector
[00:51:08] Initializing Normalizer
[00:51:08] Running Normalizer
[00:51:08] Initializing MetalDisconnector
[00:51:08] Running MetalDisconnector
[00:51:08] In

[00:51:08] Running Normalizer
[00:51:08] Running LargestFragmentChooser
[00:51:08] Fragment: CC1=CCC(C(C)C)=CC1
[00:51:08] New largest fragment: CC1=CCC(C(C)C)=CC1 (26)
[00:51:08] Running Uncharger
[00:51:08] Initializing MetalDisconnector
[00:51:08] Running MetalDisconnector
[00:51:08] Initializing Normalizer
[00:51:08] Running Normalizer
[00:51:08] Initializing MetalDisconnector
[00:51:08] Running MetalDisconnector
[00:51:08] Initializing Normalizer
[00:51:08] Running Normalizer
[00:51:08] Running LargestFragmentChooser
[00:51:08] Fragment: CCCCCC=O
[00:51:08] New largest fragment: CCCCCC=O (19)
[00:51:08] Running Uncharger
[00:51:08] Initializing MetalDisconnector
[00:51:08] Running MetalDisconnector
[00:51:08] Initializing Normalizer
[00:51:08] Running Normalizer
[00:51:08] Initializing MetalDisconnector
[00:51:08] Running MetalDisconnector
[00:51:08] Initializing Normalizer
[00:51:08] Running Normalizer
[00:51:08] Running LargestFragmentChooser
[00:51:08] Fragment: CCCCCCCCC(=O)O


[00:51:08] Running LargestFragmentChooser
[00:51:08] Fragment: C=C(C)C1CC=C(C)CC1
[00:51:08] New largest fragment: C=C(C)C1CC=C(C)CC1 (26)
[00:51:08] Running Uncharger
[00:51:08] Initializing MetalDisconnector
[00:51:08] Running MetalDisconnector
[00:51:08] Initializing Normalizer
[00:51:08] Running Normalizer
[00:51:08] Initializing MetalDisconnector
[00:51:08] Running MetalDisconnector
[00:51:08] Initializing Normalizer
[00:51:08] Running Normalizer
[00:51:08] Running LargestFragmentChooser
[00:51:08] Fragment: CC1=CC2C(CC1)C2(C)C
[00:51:08] New largest fragment: CC1=CC2C(CC1)C2(C)C (26)
[00:51:08] Running Uncharger
[00:51:08] Initializing MetalDisconnector
[00:51:08] Running MetalDisconnector
[00:51:08] Initializing Normalizer
[00:51:08] Running Normalizer
[00:51:08] Initializing MetalDisconnector
[00:51:08] Running MetalDisconnector
[00:51:08] Initializing Normalizer
[00:51:08] Running Normalizer
[00:51:08] Running LargestFragmentChooser
[00:51:08] Fragment: C=C1CCC2(C(C)C)CC12
[00

...

[00:51:22] Running LargestFragmentChooser
[00:51:22] Fragment: CC(=O)CCCC(C)CCCC(C)CCCC(C)C
[00:51:22] New largest fragment: CC(=O)CCCC(C)CCCC(C)CCCC(C)C (55)
[00:51:22] Running Uncharger
[00:51:22] Initializing MetalDisconnector
[00:51:22] Running MetalDisconnector
[00:51:22] Initializing Normalizer
[00:51:22] Running Normalizer
[00:51:22] Initializing MetalDisconnector
[00:51:22] Running MetalDisconnector
[00:51:22] Initializing Normalizer
[00:51:22] Running Normalizer
[00:51:22] Running LargestFragmentChooser
[00:51:22] Fragment: CCCCCCCCCCCCCCCCCCCCCCC
[00:51:22] New largest fragment: CCCCCCCCCCCCCCCCCCCCCCC (71)
[00:51:22] Running Uncharger
[00:51:22] Initializing MetalDisconnector
[00:51:22] Running MetalDisconnector
[00:51:22] Initializing Normalizer
[00:51:22] Running Normalizer
[00:51:22] Initializing MetalDisconnector
[00:51:22] Running MetalDisconnector
[00:51:22] Initializing Normalizer
[00:51:22] Running Normalizer
[00:51:22] Running LargestFragmentChooser
[00:51:22] Fragm

[00:51:23] Running Uncharger
[00:51:23] Initializing MetalDisconnector
[00:51:23] Running MetalDisconnector
[00:51:23] Initializing Normalizer
[00:51:23] Running Normalizer
[00:51:23] Initializing MetalDisconnector
[00:51:23] Running MetalDisconnector
[00:51:23] Initializing Normalizer
[00:51:23] Running Normalizer
[00:51:23] Running LargestFragmentChooser
[00:51:23] Fragment: CCCCCCCCCCCCCCCCCCC
[00:51:23] New largest fragment: CCCCCCCCCCCCCCCCCCC (59)
[00:51:23] Running Uncharger
[00:51:23] Initializing MetalDisconnector
[00:51:23] Running MetalDisconnector
[00:51:23] Initializing Normalizer
[00:51:23] Running Normalizer
[00:51:23] Initializing MetalDisconnector
[00:51:23] Running MetalDisconnector
[00:51:23] Initializing Normalizer
[00:51:23] Running Normalizer
[00:51:23] Running LargestFragmentChooser
[00:51:23] Fragment: CCCCOC(=O)c1ccccc1C(=O)OCC(CC)CCCC
[00:51:23] New largest fragment: CCCCOC(=O)c1ccccc1C(=O)OCC(CC)CCCC (54)
[00:51:23] Running Uncharger
[00:51:23] Initializing M

[00:51:23] Running LargestFragmentChooser
[00:51:23] Fragment: C=C1CCC2OC2(C)CCC2C1CC2(C)C
[00:51:23] New largest fragment: C=C1CCC2OC2(C)CCC2C1CC2(C)C (40)
[00:51:23] Running Uncharger
[00:51:23] Initializing MetalDisconnector
[00:51:23] Running MetalDisconnector
[00:51:23] Initializing Normalizer
[00:51:23] Running Normalizer
[00:51:23] Initializing MetalDisconnector
[00:51:23] Running MetalDisconnector
[00:51:23] Initializing Normalizer
[00:51:23] Running Normalizer
[00:51:23] Running LargestFragmentChooser
[00:51:23] Fragment: Cc1ccc2c(C)ccc(C(C)C)c2c1
[00:51:23] New largest fragment: Cc1ccc2c(C)ccc(C(C)C)c2c1 (33)
[00:51:23] Running Uncharger
[00:51:23] Initializing MetalDisconnector
[00:51:23] Running MetalDisconnector
[00:51:23] Initializing Normalizer
[00:51:23] Running Normalizer
[00:51:23] Initializing MetalDisconnector
[00:51:23] Running MetalDisconnector
[00:51:23] Initializing Normalizer
[00:51:23] Running Normalizer
[00:51:23] Running LargestFragmentChooser
[00:51:23] Fra

[00:51:23] Initializing MetalDisconnector
[00:51:23] Running MetalDisconnector
[00:51:23] Initializing Normalizer
[00:51:23] Running Normalizer
[00:51:23] Running LargestFragmentChooser
[00:51:23] Fragment: CC(C)COC(=O)c1ccccc1C(=O)OCC(C)C
[00:51:23] New largest fragment: CC(C)COC(=O)c1ccccc1C(=O)OCC(C)C (42)
[00:51:23] Running Uncharger
[00:51:23] Initializing MetalDisconnector
[00:51:23] Running MetalDisconnector
[00:51:23] Initializing Normalizer
[00:51:23] Running Normalizer
[00:51:23] Initializing MetalDisconnector
[00:51:23] Running MetalDisconnector
[00:51:23] Initializing Normalizer
[00:51:23] Running Normalizer
[00:51:23] Running LargestFragmentChooser
[00:51:23] Fragment: CCCCCCCCCCCCCCCC(=O)O
[00:51:23] New largest fragment: CCCCCCCCCCCCCCCC(=O)O (50)
[00:51:23] Running Uncharger
[00:51:23] Initializing MetalDisconnector
[00:51:23] Running MetalDisconnector
[00:51:23] Initializing Normalizer
[00:51:23] Running Normalizer
[00:51:23] Initializing MetalDisconnector
[00:51:23] R

[00:51:23] Initializing MetalDisconnector
[00:51:23] Running MetalDisconnector
[00:51:23] Initializing Normalizer
[00:51:23] Running Normalizer
[00:51:23] Running LargestFragmentChooser
[00:51:23] Fragment: CCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCC
[00:51:23] New largest fragment: CCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCC (98)
[00:51:23] Running Uncharger
[00:51:23] Initializing MetalDisconnector
[00:51:23] Running MetalDisconnector
[00:51:23] Initializing Normalizer
[00:51:23] Running Normalizer
[00:51:23] Initializing MetalDisconnector
[00:51:23] Running MetalDisconnector
[00:51:23] Initializing Normalizer
[00:51:23] Running Normalizer
[00:51:23] Running LargestFragmentChooser
[00:51:23] Fragment: CCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCC
[00:51:23] New largest fragment: CCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCCC (164)
[00:51:23] Running Uncharger
[00:51:23] Initializing MetalDisconnector
[00:51:23] Running MetalDisconnector
[00:51:23] Initializing Normalizer
[00:51:23] Runnin

In [14]:
# Compute Morgan fingerprints for test data
lst_test = np.array(
    [AllChem.GetMorganFingerprintAsBitVect(x, radius=1024) 
     for x in list(map(Chem.MolFromSmiles, good_lst_std))]
)

In [15]:
# Initialize label list
label_lst = []

# Determine if each molecule is within the Applicability Domain
for i in lst_test:
    i = i[None, :]  # Convert to 2D array for computation
    avg_distance = ad_domain.calculate_applicability_domain(i)  # Compute applicability domain
    
    if avg_distance[1][0]:  # If molecule is within AD, label as 1, otherwise 0
        label_lst.append(1)
    else:
        label_lst.append(0)

In [16]:
# Create a DataFrame containing Applicability Domain labels
df = pd.DataFrame(label_lst, columns=['label'])

In [18]:
plant = pd.read_excel('../data/plant.xlsx')

In [19]:
# create DataFrame
df = pd.DataFrame({
    'Scientific_name':plant['Scientific_name'],
    'Chinese_name':plant['Chinese_name'],
    'Extraction_site':plant['Extraction_site'],
    'Volatile_compounds':plant['Volatile_compounds'],
    'Compound_content':plant['Compound_content'],
    'Analysis_method':plant['Analysis_method'],
    'Cite':plant['Cite'],
    'SMILES':plant['SMILES'],
    'SMILES_1':plant_list,
    'Application_domain':label_lst
})

In [ ]:
gabaa = pd.read_csv('../data/gaba_smi.csv',encoding='gb18030')
gaba_smi = gabaa['SMILES']

In [21]:
#Remove duplicate data from the training set
df = df[~df['SMILES'].isin(gaba_smi)]

In [23]:
# Filter the DataFrame to exclude rows where the value in the 'Application_domain' column is 0.
df = df[df['Application_domain'] != 0]

In [45]:
# Save the results to a CSV file
df.to_excel('../data/application_domain.xlsx')